In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install torchvision==0.18.1
!pip install torch-cluster -f https://data.pyg.org/whl/torch-{torch.__version__}.html
!pip install torch_geometric

  Using cached torchvision-0.18.1-cp311-cp311-manylinux1_x86_64.whl.metadata (6.6 kB)
  Using cached torch-2.3.1-cp311-cp311-manylinux1_x86_64.whl.metadata (26 kB)
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl.met

In [ ]:
!pip install chai_lab==0.5.1
!pip install openmm
!pip install gemmi
!pip install biopython

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 74.7/74.7 kB 5.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 385.3/385.3 kB 27.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
INFO: pip is looking at multiple versions of s3fs to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.8/140.8 kB 13.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 34.4/34.4 MB 20.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.3/10.3 MB 76.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 65.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 35.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 24.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.2/117.2 kB 11.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.4/56.4 kB 4.8 MB

In [ ]:
import os, shutil
import numpy as np
import torch,torchvision

from Bio import SeqIO
from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord

from Bio.PDB import MMCIFParser, PDBIO
from Bio.PDB import PDBParser, NeighborSearch

from tqdm import tqdm
from pathlib import Path
from chai_lab.chai1 import run_inference

In [ ]:
def create_fasta_from_txt(protein_txt, output_fasta, M, num_ion):
    """
    Creates a FASTA file with protein sequences from a .txt file and adds [M+2] as a pseudo-ligand.
    It removes '+' signs and splits chains using ':'.

    Parameters:
        protein_txt (str): Path to the protein .txt file containing sequences separated by colons (:).
        output_fasta (str): Path to the output FASTA file.
    """
    fasta_entries = []

    # Extract protein sequences from the .txt file
    with open(protein_txt, 'r') as f:
        contents = f.read().strip()

    # Split on ':' to get individual chains
    chain_sequences = contents.split(':')

    # Add each protein chain to FASTA (removing '+' signs)
    for idx, seq in enumerate(chain_sequences):
        if seq != '':
            seq_clean = seq.replace('+', '').strip()  # Remove '+' signs
            chain_id = chr(ord('A') + idx)  # Label chains A, B, C, etc.
            protein_header = f"protein|name=chain_{chain_id}"

            protein_record = SeqRecord(Seq(seq_clean), id=protein_header, description="")
            fasta_entries.append(protein_record)
            print(f"    Extracted and cleaned protein sequence for chain {chain_id}")

    for i in range(num_ion):
        ligand_record = SeqRecord(
            Seq(f"[{M}+2]"), #2
            id=f"ligand|name={M.upper()}{i+1}",
            description=""
        )
        fasta_entries.append(ligand_record)

    # Write to FASTA file
    if fasta_entries:
        SeqIO.write(fasta_entries, output_fasta, "fasta")
        print(f"    FASTA file successfully written to {output_fasta}")
    else:
        print("    No entries to write to FASTA.")

In [ ]:
def add_OXT_to_pdb(input_pdb, output_pdb):
    with open(input_pdb, 'r') as infile:
        lines = infile.readlines()

    modified_lines = []
    last_residue_info = {}  # Store info for the last residue in each chain

    for line in lines:
        if line.startswith(('ATOM', 'HETATM')):
            chain_id = line[21]
            res_seq = int(line[22:26].strip())
            atom_name = line[12:16].strip()

            # Track the last residue and the carbonyl carbon 'C' atom
            if chain_id not in last_residue_info or res_seq > last_residue_info[chain_id]['res_seq']:
                last_residue_info[chain_id] = {
                    'res_seq': res_seq,
                    'C_line': line if atom_name == 'C' else None,
                }
            elif atom_name == 'C' and res_seq == last_residue_info[chain_id]['res_seq']:
                last_residue_info[chain_id]['C_line'] = line

        modified_lines.append(line)

        # Add OXT after each TER line
        if line.startswith('TER'):
            chain_id = line[21]
            if chain_id in last_residue_info:
                c_line = last_residue_info[chain_id]['C_line']
                if c_line:
                    # Extract coordinates from the C atom
                    x = float(c_line[30:38]) + 1.2  # Offset for visualization
                    y = float(c_line[38:46])
                    z = float(c_line[46:54])

                    # Generate OXT line with new atom serial number
                    new_atom_number = int(modified_lines[-2][6:11]) + 1
                    res_seq = last_residue_info[chain_id]['res_seq']

                    oxt_line = f"ATOM  {new_atom_number:5d}  OXT {c_line[17:20]} {chain_id}{res_seq:4d}    " \
                               f"{x:8.3f}{y:8.3f}{z:8.3f}  1.00  0.00           O  \n"
                    modified_lines.insert(-1, oxt_line)  # Insert before TER

    # Write the modified PDB
    with open(output_pdb, 'w') as outfile:
        outfile.writelines(modified_lines)
    os.remove(input_pdb)

In [ ]:
import gemmi
def convert_cif_to_pdb(sample_folder):
    parser = MMCIFParser(QUIET=True)
    io = PDBIO()

    # Loop through files in the folder
    for filename in os.listdir(sample_folder):
        if filename.endswith(".cif"):  # Check for CIF files
            cif_path = os.path.join(sample_folder, filename)
            # Replace .cif with .pdb
            pdb_temp_path = os.path.splitext(cif_path)[0] + "_temp.pdb"
            pdb_path = os.path.splitext(cif_path)[0] + ".pdb"

            try:
                # Parse CIF and save as PDB parser.get_structure("structure", cif_path)
                structure = gemmi.read_structure(cif_path)
                structure.write_pdb(pdb_temp_path)
                print(f"Converted '{filename}' to '{os.path.basename(pdb_temp_path)}'")

            except Exception as e:
                print(f"Failed to process '{filename}': {e}")
            add_OXT_to_pdb(pdb_temp_path, pdb_path)

In [ ]:
def run_chai(sample_folder, M, num_ion):
    """
    This function takes a single sample folder, reads the <sample_id>.txt file,
    and cofolds the proteins with Zn2+ using CHAI.
    """
    s = sample_folder
    sample_folder = Path(sample_folder)  # Ensure it's a Path object
    sample_id = sample_folder.name
    txt_file = sample_folder / f"{sample_id}.txt"

    # Loop through files in the folder
    for filename in os.listdir(s):
        if filename.endswith(f"-{num_ion}.pdb"):
            print(f"{sample_id}-{num_ion} already processed")
            return
        if filename.endswith(".fasta"):
            os.remove(f"{s}/{filename}")

    # Create FASTA from the .txt file using your provided function
    fasta_file = sample_folder / f"{sample_id}-{num_ion}.fasta"
    create_fasta_from_txt(txt_file, fasta_file, M, num_ion)

    # Create a temporary output directory to avoid CHAI conflicts
    temp_output_dir = sample_folder / "chai_output"
    temp_output_dir.mkdir(exist_ok=True)

    # Run CHAI's inference
    candidates = run_inference(
        fasta_file=fasta_file,
        output_dir=temp_output_dir,
        num_trunk_recycles=3,
        num_diffn_timesteps=200,
        seed=42,
        device=torch.device("cuda:0"),
        use_esm_embeddings=True
    )

    # Pick the top-ranked structure and copy it as <sample_id>.cif
    cif = sample_folder / f"{sample_id}-{num_ion}.cif"
    cif_paths = candidates.cif_paths
    scores = [rd.aggregate_score for rd in candidates.ranking_data]
    best_structure = cif_paths[np.argmax(scores)]
    shutil.copy(best_structure, cif)

    # Clean up temporary output directory
    shutil.rmtree(temp_output_dir)
    print(f"\n[INFO] Finished inference for '{sample_id}' -> Best structure saved.")

    # Convert cif to pdb
    convert_cif_to_pdb(sample_folder)
    os.remove(cif)

In [ ]:
def process_all_samples(M, num_ion):
    samples_dir = '/content/drive/MyDrive/Samuel/Samples'
    samples_dir += f"-{M}"

    samples_path = Path(samples_dir)  # Ensure it's a Path object
    all_sample_folders = [folder for folder in samples_path.iterdir() if folder.is_dir()]
    total_samples = len(all_sample_folders)

    for i, sample_folder in enumerate(tqdm(all_sample_folders,
                                           desc="Processing sample folders",
                                           total=total_samples)):
        if i == 100: break
        sample_id = sample_folder.name
        best_structure_path = sample_folder / f"{sample_id}-{num_ion}.cif"
        print(f"[INFO] Processing sample '{sample_id}' ({i+1}/{total_samples})")

        # Run the processing function with error handling
        try:
            run_chai(sample_folder, M, num_ion)
        except Exception as e:
            print(f"[ERROR] Failed to process sample '{sample_id}': {e}")
            continue  # Move on to the next sample even if there's an error

In [ ]:
process_all_samples("Ca",1)

Processing sample folders:   0%|          | 0/6196 [00:00<?, ?it/s]

[INFO] Processing sample '6197' (1/6196)
    Extracted and cleaned protein sequence for chain A
    FASTA file successfully written to /content/drive/MyDrive/Samuel/Samples-Ca/6197/6197-1.fasta
downloading https://chaiassets.com/chai1-inference-depencencies/conformers_v1.apkl


[04:39:13] UFFTYPER: Unrecognized atom type: Ca+2 (0)
/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/95.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/93.0 [00:00<?, ?B/s]

...


[INFO] Finished inference for '6314' -> Best structure saved.
Converted '6314-1.cif' to '6314-1_temp.pdb'
[INFO] Processing sample '6315' (100/6196)
    Extracted and cleaned protein sequence for chain A
    FASTA file successfully written to /content/drive/MyDrive/Samuel/Samples-Ca/6315/6315-1.fasta


[15:14:56] UFFTYPER: Unrecognized atom type: Ca+2 (0)

Trunk recycles: 100%|██████████| 3/3 [00:45<00:00, 15.28s/it]

Diffusion steps: 100%|██████████| 199/199 [02:29<00:00,  1.33it/s]


Score=0.0734, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_0.cif
Score=0.0725, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_1.cif
Score=0.0752, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_2.cif
Score=0.0733, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_3.cif
Score=0.0732, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_4.cif


Processing sample folders:   2%|▏         | 100/6196 [10:40:09<650:24:05, 384.10s/it]


[INFO] Finished inference for '6315' -> Best structure saved.
Converted '6315-1.cif' to '6315-1_temp.pdb'


In [ ]:
process_all_samples("Ca",2)

Processing sample folders:   0%|          | 0/6196 [00:00<?, ?it/s]

[INFO] Processing sample '6197' (1/6196)
6197-2 already processed
[INFO] Processing sample '6200' (2/6196)
6200-2 already processed
[INFO] Processing sample '6201' (3/6196)
6201-2 already processed
[INFO] Processing sample '6203' (4/6196)
6203-2 already processed
[INFO] Processing sample '6202' (5/6196)
6202-2 already processed
[INFO] Processing sample '6204' (6/6196)
6204-2 already processed
[INFO] Processing sample '6206' (7/6196)
6206-2 already processed
[INFO] Processing sample '6205' (8/6196)
6205-2 already processed
[INFO] Processing sample '6208' (9/6196)
6208-2 already processed
[INFO] Processing sample '6207' (10/6196)
6207-2 already processed
[INFO] Processing sample '6209' (11/6196)
6209-2 already processed
[INFO] Processing sample '6211' (12/6196)
6211-2 already processed
[INFO] Processing sample '6212' (13/6196)
6212-2 already processed
[INFO] Processing sample '6213' (14/6196)
6213-2 already processed
[INFO] Processing sample '6214' (15/6196)
6214-2 already processed
[INF

[18:47:04] UFFTYPER: Unrecognized atom type: Ca+2 (0)
[18:47:04] UFFTYPER: Unrecognized atom type: Ca+2 (0)
/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]


Trunk recycles:   0%|          | 0/3 [00:03<?, ?it/s]


...

[INFO] Processing sample '6315' (100/6196)
    Extracted and cleaned protein sequence for chain A
    FASTA file successfully written to /content/drive/MyDrive/Samuel/Samples-Ca/6315/6315-2.fasta


[01:11:32] UFFTYPER: Unrecognized atom type: Ca+2 (0)
[01:11:33] UFFTYPER: Unrecognized atom type: Ca+2 (0)

Trunk recycles: 100%|██████████| 3/3 [00:45<00:00, 15.23s/it]

Diffusion steps: 100%|██████████| 199/199 [02:30<00:00,  1.33it/s]


Score=0.0784, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_0.cif
Score=0.0743, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_1.cif
Score=0.0743, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_2.cif
Score=0.0778, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_3.cif
Score=0.0788, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_4.cif


Processing sample folders:   2%|▏         | 100/6196 [6:28:51<395:04:48, 233.32s/it]


[INFO] Finished inference for '6315' -> Best structure saved.
Converted '6315-1.cif' to '6315-1_temp.pdb'
Converted '6315-2.cif' to '6315-2_temp.pdb'


In [ ]:
process_all_samples("Ca",3)

Processing sample folders:   0%|          | 0/6196 [00:00<?, ?it/s]

[INFO] Processing sample '6197' (1/6196)


Processing sample folders:   0%|          | 1/6196 [00:00<41:13,  2.50it/s]

6197-3 already processed
[INFO] Processing sample '6200' (2/6196)


Processing sample folders:   0%|          | 2/6196 [00:00<43:50,  2.36it/s]

...

[INFO] Processing sample '6315' (100/6196)
    Extracted and cleaned protein sequence for chain A
    FASTA file successfully written to /content/drive/MyDrive/Samuel/Samples-Ca/6315/6315-3.fasta


[11:11:57] UFFTYPER: Unrecognized atom type: Ca+2 (0)
[11:11:58] UFFTYPER: Unrecognized atom type: Ca+2 (0)
[11:11:58] UFFTYPER: Unrecognized atom type: Ca+2 (0)

Trunk recycles: 100%|██████████| 3/3 [00:41<00:00, 13.88s/it]

Diffusion steps: 100%|██████████| 199/199 [02:22<00:00,  1.39it/s]


Score=0.0778, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_0.cif
Score=0.0736, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_1.cif
Score=0.0742, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_2.cif
Score=0.0778, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_3.cif
Score=0.0791, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_4.cif

[INFO] Finished inference for '6315' -> Best structure saved.
Converted '6315-1.cif' to '6315-1_temp.pdb'
Converted '6315-2.cif' to '6315-2_temp.pdb'


Processing sample folders:   2%|▏         | 100/6196 [6:27:19<393:31:22, 232.40s/it]

Converted '6315-3.cif' to '6315-3_temp.pdb'


In [ ]:
process_all_samples("Ca",4)

Processing sample folders:   0%|          | 0/6196 [00:00<?, ?it/s]

[INFO] Processing sample '6197' (1/6196)
    Extracted and cleaned protein sequence for chain A
    FASTA file successfully written to /content/drive/MyDrive/Samuel/Samples-Ca/6197/6197-4.fasta


[11:16:09] UFFTYPER: Unrecognized atom type: Ca+2 (0)
[11:16:09] UFFTYPER: Unrecognized atom type: Ca+2 (0)
[11:16:10] UFFTYPER: Unrecognized atom type: Ca+2 (0)
[11:16:10] UFFTYPER: Unrecognized atom type: Ca+2 (0)

Trunk recycles: 100%|██████████| 3/3 [00:42<00:00, 14.21s/it]

Diffusion steps: 100%|██████████| 199/199 [02:25<00:00,  1.36it/s]


Score=0.0360, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6197/chai_output/pred.model_idx_0.cif
Score=0.0364, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6197/chai_output/pred.model_idx_1.cif
Score=0.0362, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6197/chai_output/pred.model_idx_2.cif
Score=0.0360, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6197/chai_output/pred.model_idx_3.cif
Score=0.0360, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6197/chai_output/pred.model_idx_4.cif

[INFO] Finished inference for '6197' -> Best structure saved.
Converted '6197-1.cif' to '6197-1_temp.pdb'
Converted '6197-2.cif' to '6197-2_temp.pdb'
Converted '6197-3.cif' to '6197-3_temp.pdb'


Processing sample folders:   0%|          | 1/6196 [04:17<443:31:50, 257.74s/it]

...

[INFO] Processing sample '6315' (100/6196)
    Extracted and cleaned protein sequence for chain A
    FASTA file successfully written to /content/drive/MyDrive/Samuel/Samples-Ca/6315/6315-4.fasta


[19:16:49] UFFTYPER: Unrecognized atom type: Ca+2 (0)
[19:16:50] UFFTYPER: Unrecognized atom type: Ca+2 (0)
[19:16:51] UFFTYPER: Unrecognized atom type: Ca+2 (0)
[19:16:51] UFFTYPER: Unrecognized atom type: Ca+2 (0)

Trunk recycles: 100%|██████████| 3/3 [00:41<00:00, 13.88s/it]

Diffusion steps: 100%|██████████| 199/199 [02:22<00:00,  1.39it/s]


Score=0.0773, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_0.cif
Score=0.0727, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_1.cif
Score=0.0734, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_2.cif
Score=0.0769, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_3.cif
Score=0.0764, writing output to /content/drive/MyDrive/Samuel/Samples-Ca/6315/chai_output/pred.model_idx_4.cif


Processing sample folders:   2%|▏         | 100/6196 [8:04:50<492:36:14, 290.91s/it]


[INFO] Finished inference for '6315' -> Best structure saved.
Converted '6315-1.cif' to '6315-1_temp.pdb'
Converted '6315-2.cif' to '6315-2_temp.pdb'
Converted '6315-4.cif' to '6315-4_temp.pdb'
